In [2]:
import pandas as pd
import numpy as np
from datetime import datetime
import scipy.stats as sp
import scipy.optimize as sco
from scipy.linalg import solve
from scipy.interpolate import CubicSpline
import plotly
from plotly import graph_objs as go
from plotly.subplots import make_subplots
plotly.offline.init_notebook_mode(connected = True)

In [3]:
def BSM(S0, K, tau, r, sigma, opt_type='c', q=0):
    d1 = (np.log(S0/K)+(r-q+.5*sigma**2)*tau)/(sigma*np.sqrt(tau))
    d2 = d1 - sigma*np.sqrt(tau)
    N = lambda x: sp.norm.cdf(x)
    if opt_type == 'c':
        return S0*np.exp(-q*tau)*N(d1) - np.exp(-r*tau)*K*N(d2)
    else:
        return K*np.exp(-r*tau)*N(-d2) - S0*np.exp(-q*tau)*N(-d1)

In [4]:
files = ['20180427', '20180504', '20180511', '20180518', '20180525', '20180601', '20180608', '20180615',
        '20180720', '20180817', '20180921', '20181019', '20181116', '20190118', '20190215', '20190621',
        '20200117']
r = 0.0184 # 3m Treasury 4/30/18
dfs = []
for f in files:
    temp = pd.read_csv('{}.csv'.format(f))
    temp['TTM'] = (pd.to_datetime(temp['T'].apply(lambda x: str(x))) - pd.datetime(2018,4,27)).apply(lambda x: x.days)/365
    dfs.append(temp)
S = dfs[0].S[0]
dfs[0].TTM = 1/365
dfs

[     Unnamed: 0         T       K   P_bid   P_ask   C_bid   C_ask        S  \
 0             0  20180427   910.0    0.00    0.02  607.10  611.80  1517.96   
 1             1  20180427   920.0    0.00    0.03  596.50  601.50  1517.96   
 2             2  20180427   930.0    0.00    3.80  586.70  591.70  1517.96   
 3             3  20180427   940.0    0.00    0.05  576.50  581.50  1517.96   
 4             4  20180427   950.0    0.00    0.05  566.50  571.50  1517.96   
 5             5  20180427   960.0    0.00    1.67  556.40  561.40  1517.96   
 6             6  20180427   970.0    0.00    3.35  546.50  551.50  1517.96   
 7             7  20180427   980.0    0.00    4.25  536.50  541.50  1517.96   
 8             8  20180427   990.0    0.00    0.68  526.55  531.55  1517.96   
 9             9  20180427  1000.0    0.00    0.04  516.55  521.55  1517.96   
 10           10  20180427  1010.0    0.00    0.68  506.55  511.55  1517.96   
 11           11  20180427  1020.0    0.00    0.08  

In [5]:
tol = 10E-9
def SVI(df,a,b,p,m,sig):
    k = np.log(np.asarray(df.K)/1517.96)
    return a + b*(p*(np.asarray(k)-m) + np.sqrt((np.asarray(k)-m)**2 + sig**2))

        
def SVI_fit(df,IV_col):
    obj = lambda x: np.sum((SVI(df, x[0], x[1], x[2], x[3], x[4]) - np.asarray(df[IV_col]))**2)
    cons = ({'type':'ineq','fun': lambda x: x[0] + x[1]*x[4]*np.sqrt(1 - x[2]**2)},
            {'type':'ineq','fun': lambda x: x[1]},
            {'type':'ineq','fun': lambda x: x[4] - tol})
    bnds = ((None,None),(0,None),(-1+tol,1-tol),(None,None),(tol,None))
    guess = [.01,.01,.01,.01,.01]
    result = sco.minimize(obj,guess,constraints=cons,bounds=bnds,tol=tol)
    return result

SVI_fit(dfs[0],'Comb_vol')

     fun: 1.6554086383917688
     jac: array([-0.00085485, -0.00035636,  0.00061601,  0.0002605 , -0.00642359])
 message: 'Optimization terminated successfully.'
    nfev: 371
     nit: 49
    njev: 49
  status: 0
 success: True
       x: array([-2.19721984, 11.73399722,  0.11266262,  0.04544888,  0.28812271])

In [6]:
temp = dfs[0]
fit1 = SVI_fit(temp[temp.K < S],'Comb_vol')['x']
fit2 = SVI_fit(temp[temp.K > S],'Comb_vol')['x']

In [7]:
temp['SVI'] = np.append(SVI(temp[temp.K < S],fit1[0],fit1[1],fit1[2],fit1[3],fit1[4]),
          SVI(temp[temp.K > S],fit2[0],fit2[1],fit2[2],fit2[3],fit2[4]), axis=0)
# temp['SVI'] = np.append(SVI(temp[temp.K < S],fit1_derivs[0],fit1_derivs[1],fit1_derivs[2],
#                             fit1_derivs[3],fit1_derivs[4]),
#           SVI(temp[temp.K > S],fit2[0],fit2[1],fit2[2],fit2[3],fit2[4]), axis=0)
temp.head()

Unnamed: 0         T      K  P_bid  P_ask  C_bid  C_ask        S     dS  \
0           0  20180427  910.0    0.0   0.02  607.1  611.8  1517.96  0.001   
1           1  20180427  920.0    0.0   0.03  596.5  601.5  1517.96  0.001   
2           2  20180427  930.0    0.0   3.80  586.7  591.7  1517.96  0.001   
3           3  20180427  940.0    0.0   0.05  576.5  581.5  1517.96  0.001   
4           4  20180427  950.0    0.0   0.05  566.5  571.5  1517.96  0.001   

   Comb_vol      TTM       SVI  
0  4.495669  0.00274  4.322827  
1  4.191422  0.00274  4.238463  
2  4.211310  0.00274  4.155022  
3  4.028153  0.00274  4.072486  
4  3.947705  0.00274  3.990835

In [7]:
trace0 = go.Scatter(
    x = temp.K, y = temp.Comb_vol, name = 'Implied Vol'
)
trace1 = go.Scatter(
    x = temp.K, y = temp.SVI, name = 'SVI'
)
data = [trace0,trace1]
layout = go.Layout(
    title = 'SVI Interpolated Implied Volatility', 
    yaxis = dict(title = 'Implied Volatility (%)'), xaxis = dict(title = 'Strike'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [8]:
df427 = pd.DataFrame({'K': np.linspace(800,2200,2801), 'TTM': dfs[0].TTM[0]})
df427['SVI'] = np.append(SVI(df427[df427.K < S],fit1[0],fit1[1],fit1[2],fit1[3],fit1[4]),
          SVI(df427[df427.K > S],fit2[0],fit2[1],fit2[2],fit2[3],fit2[4]), axis=0)
df427['C'] = df427.apply(lambda x: BSM(S,x.K,x.TTM,r,x.SVI), axis=1)
df427['PDF'] = (df427.C.shift(-1) - 2*df427.C + df427.C.shift(1))/.5**2
df427

K      TTM       SVI           C           PDF
0      800.0  0.00274  5.317928  719.110533           NaN
1      800.5  0.00274  5.313100  718.610419  3.809491e-07
2      801.0  0.00274  5.308275  718.110305  3.839100e-07
3      801.5  0.00274  5.303453  717.610190  3.868768e-07
4      802.0  0.00274  5.298634  717.110076  3.898444e-07
5      802.5  0.00274  5.293818  716.609962  3.928208e-07
6      803.0  0.00274  5.289005  716.109849  3.958035e-07
7      803.5  0.00274  5.284196  715.609735  3.987898e-07
8      804.0  0.00274  5.279389  715.109621  4.017807e-07
9      804.5  0.00274  5.274585  714.609508  4.047802e-07
10     805.0  0.00274  5.269784  714.109394  4.077801e-07
11     805.5  0.00274  5.264986  713.609281  4.107933e-07
12     806.0  0.00274  5.260191  713.109168  4.138033e-07
13     806.5  0.00274  5.255399  712.609055  4.168255e-07
14     807.0  0.00274  5.250610  712.108942  4.198500e-07
15     807.5  0.00274  5.245825  711.608829  4.228827e-07
16     808.0  0.00274  5.241042  711.108716  4.259182e-07
17     808.5  0.00274  5.236262  710.608603  4.289614e-07
18     809.0  0.00274  5.231485  710.108490  4.320113e-07
19     809.5  0.00274  5.226711  709.608378  4.350627e-07
20     810.0  0.00274  5.221940  709.108266  4.381254e-07
21     810.5  0.00274  5.217172  708.608153  4.411904e-07
22     811.0  0.00274  5.212406  708.108041  4.442622e-07
23     811.5  0.00274  5.207644  707.607929  4.473413e-07
24     812.0  0.00274  5.202885  707.107817  4.504236e-07
25     812.5  0.00274  5.198129  706.607705  4.535154e-07
26     813.0  0.00274  5.193375  706.107594  4.566100e-07
27     813.5  0.00274  5.188625  705.607482  4.597123e-07
28     814.0  0.00274  5.183877  705.107370  4.628205e-07
29     814.5  0.00274  5.179133  704.607259  4.659360e-07
...      ...      ...       ...         ...           ...
2771  2185.5  0.00274  3.135797    1.375048  1.240492e-06
2772  2186.0  0.00274  3.137549    1.375367  1.236879e-06
2773  2186.5  0.00274  3.139301    1.375687  1.233280e-06
2774  2187.0  0.00274  3.141052    1.376006  1.229694e-06
2775  2187.5  0.00274  3.142803    1.376327  1.226120e-06
2776  2188.0  0.00274  3.144554    1.376647  1.222560e-06
2777  2188.5  0.00274  3.146305    1.376968  1.219013e-06
2778  2189.0  0.00274  3.148055    1.377289  1.215478e-06
2779  2189.5  0.00274  3.149804    1.377610  1.211956e-06
2780  2190.0  0.00274  3.151553    1.377932  1.208448e-06
2781  2190.5  0.00274  3.153302    1.378254  1.204952e-06
2782  2191.0  0.00274  3.155051    1.378577  1.201468e-06
2783  2191.5  0.00274  3.156799    1.378899  1.197997e-06
2784  2192.0  0.00274  3.158547    1.379222  1.194539e-06
2785  2192.5  0.00274  3.160294    1.379545  1.191092e-06
2786  2193.0  0.00274  3.162041    1.379869  1.187659e-06
2787  2193.5  0.00274  3.163788    1.380193  1.184237e-06
2788  2194.0  0.00274  3.165534    1.380517  1.180829e-06
2789  2194.5  0.00274  3.167280    1.380841  1.177432e-06
2790  2195.0  0.00274  3.169026    1.381166  1.174047e-06
2791  2195.5  0.00274  3.170771    1.381491  1.170675e-06
2792  2196.0  0.00274  3.172516    1.381816  1.167315e-06
2793  2196.5  0.00274  3.174260    1.382142  1.163967e-06
2794  2197.0  0.00274  3.176004    1.382468  1.160630e-06
2795  2197.5  0.00274  3.177748    1.382794  1.157306e-06
2796  2198.0  0.00274  3.179491    1.383120  1.153993e-06
2797  2198.5  0.00274  3.181234    1.383447  1.150693e-06
2798  2199.0  0.00274  3.182977    1.383774  1.147404e-06
2799  2199.5  0.00274  3.184719    1.384101  1.144127e-06
2800  2200.0  0.00274  3.186461    1.384429           NaN

[2801 rows x 5 columns]

In [10]:
temp2 = df427[(df427['K'] <= 1517) | (df427['K'] >= 1518.5)]
trace = go.Scatter(x = df427['K'], 
                   y = df427['PDF'] , name = 'f(S)')
# trace = go.Scatter(x = temp2['K'], 
#                    y = temp2.PDF, name = 'f(S)')
trace1 = go.Scatter(x = 2*[S], y = [min(temp2.dropna()['PDF']),max(temp2.dropna()['PDF'])],
                    mode = 'lines', name = 'Underlying')
data = [trace,trace1]
layout = go.Layout(title = 'AMZN PDF: 4-27-2018', yaxis = dict(title = 'Probability Density'), xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [8]:
def cs(x,y):
    n = len(y)
    R_vec = np.append(np.array(y),np.array((0,0)))
    t = np.array(x)
    A = np.zeros((n+2,n+2))
    plus = lambda x: max(x,0)
    t1 = t[0]
    for i in range(n):
        c2 = t[i] - t1
        A[i,] = [1, c2, c2**2] + [plus(t[i] - t[j])**3 for j in range(n-1)]
    A[n,] = [0,0,2] + [0]*(n-1)
    A[n+1,] = [0,0,2] + [6*plus(t[n-1] - t[k]) for k in range(n-1)]
    return np.dot(np.linalg.inv(A),R_vec)

temp2 = temp[temp.index.isin(np.arange(0,303,20))].reset_index(drop=True)
k = np.log(np.asarray(temp2.K)/1517.96)
coef = cs(temp2.K,temp2['SVI'])
ind = ['a', 'b', 'c'] + ['d{}'.format(i) for i in range(1,len(k))]
pd.DataFrame({'Coefficient': coef}, index = ind)

Coefficient
a    4.322827e+00
b   -7.975865e-03
c   -6.053677e-16
d1   8.094219e-09
d2  -1.442665e-08
d3   1.852026e-08
d4   2.982144e-08
d5   1.459913e-07
d6  -3.732296e-07
d7   1.573323e-07
d8  -3.476602e-07
d9   8.767761e-07
d10 -5.300878e-07
d11  1.106358e-08
d12 -7.750993e-08
d13  7.415656e-08
d14  1.006123e-08
d15  1.211017e-08

In [9]:
def interpolate(t_int, x, y):
    n = len(t_int)
    coef = cs(x,y)
    plus = lambda x: max(x,0)
    y_int = np.zeros(n)
    for i in range(n):
        temp = t_int[i] - x[0]
        y_int[i] = \
        sum([coef[0],coef[1]*temp,coef[2]*temp**2]+[coef[j+3]*plus(t_int[i]-x[j])**3 for j in range(len(coef)-3)])
    return y_int

t_int = np.linspace(800,2200,5601)
y_int = interpolate(t_int, temp2.K, temp2['SVI'])

trace1 = go.Scatter(
    x = temp.K, y = 100*temp['SVI'], name = 'SVI Implied Vol'
)
trace2 = go.Scatter(
    x = t_int, y = y_int*100, name = 'CS Implied Vol'
)
trace3 = go.Scatter(
    x = temp.K, y = 100*temp.Comb_vol, name = 'Implied Vol'
)

data = [trace3, trace1, trace2]
layout = go.Layout(
    title = 'Cubic Spline Interpolated Implied Volatility', 
    yaxis = dict(title = 'Implied Volatility (%)'), xaxis = dict(title = 'Strike'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [10]:
df427CS = pd.DataFrame({'K': t_int, 'TTM': dfs[0].TTM[0], 'Sigma': y_int})
df427CS['C'] = df427CS.apply(lambda x: BSM(S,x.K,x.TTM,r,x.Sigma), axis=1)
df427CS['PDF'] = (df427CS.C.shift(-1) - 2*df427CS.C + df427CS.C.shift(1))/.25**2
df427CS

K      TTM     Sigma           C       PDF
0      800.00  0.00274  5.200173  718.931449       NaN
1      800.25  0.00274  5.198179  718.681936 -0.000007
2      800.50  0.00274  5.196185  718.432422 -0.000007
3      800.75  0.00274  5.194191  718.182908 -0.000007
4      801.00  0.00274  5.192197  717.933394 -0.000007
5      801.25  0.00274  5.190203  717.683879 -0.000007
6      801.50  0.00274  5.188209  717.434363 -0.000007
7      801.75  0.00274  5.186215  717.184847 -0.000007
8      802.00  0.00274  5.184221  716.935331 -0.000008
9      802.25  0.00274  5.182227  716.685814 -0.000008
10     802.50  0.00274  5.180233  716.436296 -0.000008
11     802.75  0.00274  5.178239  716.186779 -0.000008
12     803.00  0.00274  5.176245  715.937260 -0.000008
13     803.25  0.00274  5.174251  715.687742 -0.000008
14     803.50  0.00274  5.172257  715.438222 -0.000008
15     803.75  0.00274  5.170263  715.188702 -0.000008
16     804.00  0.00274  5.168269  714.939182 -0.000008
17     804.25  0.00274  5.166275  714.689662 -0.000008
18     804.50  0.00274  5.164281  714.440140 -0.000008
19     804.75  0.00274  5.162287  714.190619 -0.000008
20     805.00  0.00274  5.160293  713.941097 -0.000008
21     805.25  0.00274  5.158299  713.691574 -0.000008
22     805.50  0.00274  5.156305  713.442051 -0.000008
23     805.75  0.00274  5.154311  713.192527 -0.000008
24     806.00  0.00274  5.152317  712.943003 -0.000008
25     806.25  0.00274  5.150323  712.693479 -0.000008
26     806.50  0.00274  5.148329  712.443954 -0.000008
27     806.75  0.00274  5.146335  712.194428 -0.000008
28     807.00  0.00274  5.144341  711.944902 -0.000008
29     807.25  0.00274  5.142347  711.695376 -0.000008
...       ...      ...       ...         ...       ...
5571  2192.75  0.00274  3.184934    1.457472  0.000008
5572  2193.00  0.00274  3.185888    1.457893  0.000008
5573  2193.25  0.00274  3.186842    1.458314  0.000008
5574  2193.50  0.00274  3.187796    1.458736  0.000008
5575  2193.75  0.00274  3.188750    1.459159  0.000008
5576  2194.00  0.00274  3.189704    1.459581  0.000008
5577  2194.25  0.00274  3.190658    1.460005  0.000008
5578  2194.50  0.00274  3.191612    1.460429  0.000008
5579  2194.75  0.00274  3.192566    1.460853  0.000008
5580  2195.00  0.00274  3.193521    1.461278  0.000008
5581  2195.25  0.00274  3.194475    1.461703  0.000008
5582  2195.50  0.00274  3.195429    1.462129  0.000008
5583  2195.75  0.00274  3.196384    1.462556  0.000008
5584  2196.00  0.00274  3.197338    1.462982  0.000008
5585  2196.25  0.00274  3.198292    1.463410  0.000008
5586  2196.50  0.00274  3.199247    1.463838  0.000008
5587  2196.75  0.00274  3.200202    1.464266  0.000008
5588  2197.00  0.00274  3.201156    1.464695  0.000008
5589  2197.25  0.00274  3.202111    1.465125  0.000008
5590  2197.50  0.00274  3.203065    1.465555  0.000008
5591  2197.75  0.00274  3.204020    1.465985  0.000008
5592  2198.00  0.00274  3.204975    1.466416  0.000008
5593  2198.25  0.00274  3.205930    1.466847  0.000008
5594  2198.50  0.00274  3.206885    1.467279  0.000008
5595  2198.75  0.00274  3.207840    1.467712  0.000008
5596  2199.00  0.00274  3.208795    1.468145  0.000008
5597  2199.25  0.00274  3.209750    1.468578  0.000008
5598  2199.50  0.00274  3.210705    1.469012  0.000008
5599  2199.75  0.00274  3.211660    1.469447  0.000008
5600  2200.00  0.00274  3.212615    1.469882       NaN

[5601 rows x 5 columns]

In [11]:
trace = go.Scatter(x = df427CS['K'], y = df427CS.PDF, name = 'f(S)')
trace2 = go.Scatter(x = 10*[1572.62], y = np.linspace(0,0.0057,10), name = 'Underlying', mode='lines')
data = [trace,trace2]
layout = go.Layout(title = 'AMZN PDF: 4-27-2018', yaxis = dict(title = 'Probability Density'), xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [14]:
len(temp)

304

In [12]:
df427CS = pd.DataFrame({'K': t_int, 'TTM': dfs[0].TTM[0]})

for i in [10,20,30,40,50]:
    temp2 = temp[temp.index.isin(np.arange(0,303,i))].reset_index(drop=True)
    y_int = interpolate(t_int, temp2.K, temp2['SVI'])
    df427CS['Sigma{}'.format(len(temp2))] = y_int
    tempC = df427CS.apply(lambda x: BSM(S,x.K,x.TTM,r,x['Sigma{}'.format(len(temp2))]),axis=1)
    df427CS['C{}'.format(len(temp2))] = tempC
    df427CS['PDF{}'.format(len(temp2))] = (tempC.shift(-1)-2*tempC+tempC.shift(1))/.25**2
df427CS

K      TTM   Sigma31         C31     PDF31   Sigma16         C16  \
0      800.00  0.00274  5.226299  718.969324       NaN  5.200173  718.931449   
1      800.25  0.00274  5.224245  718.719752 -0.000009  5.198179  718.681936   
2      800.50  0.00274  5.222192  718.470179 -0.000009  5.196185  718.432422   
3      800.75  0.00274  5.220139  718.220606 -0.000009  5.194191  718.182908   
4      801.00  0.00274  5.218085  717.971032 -0.000009  5.192197  717.933394   
5      801.25  0.00274  5.216032  717.721457 -0.000009  5.190203  717.683879   
6      801.50  0.00274  5.213979  717.471882 -0.000009  5.188209  717.434363   
7      801.75  0.00274  5.211925  717.222306 -0.000009  5.186215  717.184847   
8      802.00  0.00274  5.209872  716.972729 -0.000009  5.184221  716.935331   
9      802.25  0.00274  5.207819  716.723152 -0.000009  5.182227  716.685814   
10     802.50  0.00274  5.205765  716.473575 -0.000010  5.180233  716.436296   
11     802.75  0.00274  5.203712  716.223996 -0.000010  5.178239  716.186779   
12     803.00  0.00274  5.201659  715.974418 -0.000010  5.176245  715.937260   
13     803.25  0.00274  5.199605  715.724838 -0.000010  5.174251  715.687742   
14     803.50  0.00274  5.197552  715.475258 -0.000010  5.172257  715.438222   
15     803.75  0.00274  5.195499  715.225677 -0.000010  5.170263  715.188702   
16     804.00  0.00274  5.193445  714.976096 -0.000010  5.168269  714.939182   
17     804.25  0.00274  5.191392  714.726514 -0.000010  5.166275  714.689662   
18     804.50  0.00274  5.189338  714.476932 -0.000010  5.164281  714.440140   
19     804.75  0.00274  5.187285  714.227349 -0.000010  5.162287  714.190619   
20     805.00  0.00274  5.185232  713.977765 -0.000010  5.160293  713.941097   
21     805.25  0.00274  5.183178  713.728181 -0.000010  5.158299  713.691574   
22     805.50  0.00274  5.181125  713.478596 -0.000010  5.156305  713.442051   
23     805.75  0.00274  5.179072  713.229011 -0.000010  5.154311  713.192527   
24     806.00  0.00274  5.177018  712.979425 -0.000010  5.152317  712.943003   
25     806.25  0.00274  5.174965  712.729838 -0.000010  5.150323  712.693479   
26     806.50  0.00274  5.172912  712.480251 -0.000010  5.148329  712.443954   
27     806.75  0.00274  5.170858  712.230663 -0.000010  5.146335  712.194428   
28     807.00  0.00274  5.168805  711.981075 -0.000010  5.144341  711.944902   
29     807.25  0.00274  5.166752  711.731486 -0.000010  5.142347  711.695376   
...       ...      ...       ...         ...       ...       ...         ...   
5571  2192.75  0.00274  3.181056    1.444587  0.000011  3.184934    1.457472   
5572  2193.00  0.00274  3.182009    1.445006  0.000011  3.185888    1.457893   
5573  2193.25  0.00274  3.182962    1.445426  0.000011  3.186842    1.458314   
5574  2193.50  0.00274  3.183916    1.445846  0.000011  3.187796    1.458736   
5575  2193.75  0.00274  3.184870    1.446267  0.000011  3.188750    1.459159   
5576  2194.00  0.00274  3.185823    1.446689  0.000011  3.189704    1.459581   
5577  2194.25  0.00274  3.186777    1.447111  0.000011  3.190658    1.460005   
5578  2194.50  0.00274  3.187731    1.447534  0.000011  3.191612    1.460429   
5579  2194.75  0.00274  3.188685    1.447957  0.000011  3.192566    1.460853   
5580  2195.00  0.00274  3.189639    1.448382  0.000011  3.193521    1.461278   
5581  2195.25  0.00274  3.190593    1.448807  0.000011  3.194475    1.461703   
5582  2195.50  0.00274  3.191548    1.449232  0.000011  3.195429    1.462129   
5583  2195.75  0.00274  3.192502    1.449659  0.000011  3.196384    1.462556   
5584  2196.00  0.00274  3.193457    1.450086  0.000011  3.197338    1.462982   
5585  2196.25  0.00274  3.194411    1.450513  0.000011  3.198292    1.463410   
5586  2196.50  0.00274  3.195366    1.450942  0.000011  3.199247    1.463838   
5587  2196.75  0.00274  3.196321    1.451371  0.000011  3.200202    1.464266   
5588  2197.00  0.00274  3.197275    1.451801  0.000011  3.201156    1.464695   
5589  2197.2

In [13]:
trace1 = go.Scatter(
    x = temp.K, y = 100*temp.Comb_vol, name = 'Implied Vol'
)
data = [trace1]
for i in [31, 16, 11, 8, 7]:
    trace = go.Scatter(
        x = t_int, y = df427CS['Sigma{}'.format(i)]*100, name = 'CS Implied Vol {} Points'.format(i)
    )
    data.append(trace)


layout = go.Layout(
    title = 'Cubic Spline Interpolated Implied Volatility', 
    yaxis = dict(title = 'Implied Volatility (%)'), xaxis = dict(title = 'Strike'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [83]:
trace1 = go.Scatter(x = 10*[1572.62], y = np.linspace(-.15,0.65,10), name = 'Underlying', mode = 'lines')
data = [trace1]

for i in [31, 16, 11, 8, 7]:
    trace = go.Scatter(
        x = t_int, y = df427CS['PDF{}'.format(i)]*100, name = 'CS f(S) {} Points'.format(i)
    )
    data.append(trace)

layout = go.Layout(title = 'AMZN PDF: 4-27-2018',yaxis = dict(title = 'Probability Density'),xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)